In [62]:
import numpy as np
import pandas as pd
from nltk.tokenize import TweetTokenizer
from gensim.models.keyedvectors import KeyedVectors
from collections import defaultdict
from sklearn import metrics
import re
from collections import defaultdict
from nltk.corpus import stopwords

In [171]:
from keras.models import Sequential, model_from_json
from keras.layers.core import Dropout, Dense, Activation
from keras.layers.embeddings import Embedding
from keras.layers.recurrent import LSTM
from keras.layers.convolutional import Convolution1D, MaxPooling1D
from keras.callbacks import ModelCheckpoint
from keras.callbacks import EarlyStopping
from keras.optimizers import Adam
from keras.utils import np_utils
from keras.layers import Embedding

In [4]:
data = pd.read_csv('Train_v1.tsv', header=None, sep='\t')

In [5]:
data.columns = ["ff", "label", "stmt"]
data.head()

ff  label                                               stmt
0  TrainSen      0  @0430yes i hope youre lurking rn. i want to li...
1  TrainSen      0  05 really taught me a valuable lesson I'm neve...
2  TrainSen      0  @098BERRY Never had a voice to protest, so you...
3  TrainSen      0  @0hMySt4rs Rest in peace & love to you and you...
4  TrainSen      0  100 days until Christmas! 🌲 #too soon #not rea...

In [6]:
label = data.label.tolist()
stmt = data.stmt.tolist()

In [138]:
repl = {
    "&lt;3": " good ",
    ":d": " good ",
    ":dd": " good ",
    ":p": " good ",
    "8)": " good ",
    ":-)": " good ",
    ":)": " good ",
    ";)": " good ",
    "(-:": " good ",
    "(:": " good ",
    "yay!": " good ",
    "yay": " good ",
    "yaay": " good ",
    "yaaay": " good ",
    "yaaaay": " good ",
    "yaaaaay": " good ",
    ":/": " bad ",
    ":&gt;": " sad ",
    ":')": " sad ",
    ":-(": " bad ",
    ":(": " bad ",
    ":s": " bad ",
    ":-s": " bad ",
    "&lt;3": " heart ",
    ":d": " smile ",
    ":p": " smile ",
    ":dd": " smile ",
    "8)": " smile ",
    ":-)": " smile ",
    ":)": " smile ",
    ";)": " smile ",
    "(-:": " smile ",
    "(:": " smile ",
    ":/": " worry ",
    ":&gt;": " angry ",
    ":')": " sad ",
    ":-(": " sad ",
    ":(": " sad ",
    ":s": " sad ",
    ":-s": " sad ",
    r"\br\b": "are",
    r"\bu\b": "you",
    r"\bhaha\b": "ha",
    r"\bhahaha\b": "ha",
    r"\bdon't\b": "do not",
    r"\bdoesn't\b": "does not",
    r"\bdidn't\b": "did not",
    r"\bhasn't\b": "has not",
    r"\bhaven't\b": "have not",
    r"\bhadn't\b": "had not",
    r"\bwon't\b": "will not",
    r"\bwouldn't\b": "would not",
    r"\bcan't\b": "can not",
    r"\bcannot\b": "can not",
    r"\bi'm\b": "i am",
    "m": "am",
    "r": "are",
    "u": "you",
    "haha": "ha",
    "hahaha": "ha",
    "don't": "do not",
    "doesn't": "does not",
    "didn't": "did not",
    "hasn't": "has not",
    "haven't": "have not",
    "hadn't": "had not",
    "won't": "will not",
    "wouldn't": "would not",
    "can't": "can not",
    "cannot": "can not",
    "i'm": "i am",
    "m": "am",
    "i'll" : "i will"
}

In [58]:
emoji_dict = defaultdict()
with open('emoji_unicode_names_final.txt', 'r', encoding="utf8") as f:
    lines = f.readlines()
    for line in lines:
        tokens = line.strip().split('\t')
        emoji_dict[tokens[0]] = tokens[1]
# emoji_dict

defaultdict(None,
            {'💫': 'dizzy_symbol',
             '😹': 'cat_face_with_tears_of_joy',
             '🇻🇬': 'British_Virgin_Islands',
             '🏊\u200d♂️': 'man_swimming',
             '🕴': 'man_in_business_suit_levitating',
             '🍝': 'spaghetti',
             '🙆': 'face_with_ok_gesture',
             '👨\u200d🔧': 'male_mechanic',
             '💦': 'splashing_sweat_symbol',
             '👩\u200d👩\u200d👧\u200d👧': 'woman_woman_girl_girl',
             '🇳🇷': 'Nauru',
             '👲': 'man_with_gua_pi_mao',
             '⛰': 'mountain',
             '🚌': 'bus',
             '↗': 'north_east_arrow',
             '🈶': 'squared_cjk_unified_ideograph_6709',
             '🏊': 'swimmer',
             '🗾': 'silhouette_of_japan',
             '🚯': 'do_not_litter_symbol',
             '🍻': 'clinking_beer_mugs',
             '🏔': 'snow_capped_mountain',
             '🚁': 'helicopter',
             '➕': 'heavy_plus_sign',
             '👎': 'thumbs_down_sign',
             '🇭🇰':

In [59]:
j = 0
for string in stmt:
    i += 1
    print(string.split())
    if i == 20:
        break

['@0430yes', 'i', 'hope', 'youre', 'lurking', 'rn.', 'i', 'want', 'to', 'listen', 'to', 'hallucination', '&', 'wanna', 'love', 'you', 'again', 'live', 'someday,', 'pretty', 'please?!', '😭', '😭', '😭']
['05', 'really', 'taught', 'me', 'a', 'valuable', 'lesson', "I'm", 'never', 'gonna', 'be', 'late', 'again!', '#Not']
['@098BERRY', 'Never', 'had', 'a', 'voice', 'to', 'protest,', 'so', 'you', 'fed', 'me', 'shit', 'to', 'digest.', 'I', 'wish', 'I', 'had', 'a', 'reason,', 'my', 'flaws', 'are', 'open', 'season.']
['@0hMySt4rs', 'Rest', 'in', 'peace', '&', 'love', 'to', 'you', 'and', 'your', 'family']
['100', 'days', 'until', 'Christmas!', '🌲', '#too', 'soon', '#not', 'ready', 'yet']
['@100_ThingsILove', '@WhatNinaSpotted', 'yay!', "Can't", 'wait', 'to', 'be', 'reunited', 'with', 'you', 'huni!', 'Xx']
['100', 'words', 'short', 'of', 'the', 'word', 'requirement', 'but', 'I', "don't", 'care,', "I'm", 'going', 'to', 'bed.', '#rebel', '#ihatehistory']
['@1010xlhacker', 'it', 'was', 'nice', 'hangin

['@ABC', 'customers', 'fault', 'for', 'trusting', 'banks', 'and', 'computers', 'never', 'trust', 'anybody', 'especially', 'not', 'technology', '☺']
['@ABC', 'Hey,', 'if', 'your', 'gonna', 'all', 'cheat', 'you', 'might', 'as', 'well', 'all', 'cheat.']
['@ABC', 'it', "didn't", 'help', 'his', 'cause', 'to', 'destroy', 'our', 'country', "that's", 'why']
['@ABC', 'I', 'think', 'everyone', 'should', 'calm', 'the', 'f**k', 'down', '&', 'wait', 'until', 'he', 'actually', 'does', 'something', 'before', 'we', 'get', 'mad.', 'Protesting', 'results', 'does', 'NOTHING!']
['@ABC', 'Pathetic', 'people', 'DESTROY', 'their', 'cause', 'a', 'little', 'more', 'each', 'day!']
['@ABCPolitics', 'I', 'am', 'so', 'happy', 'to', 'see', 'the', 'humble', 'side', 'of', '#Trump', 'come', 'out', 'in', 'Louisiana.', 'He', 'truly', 'did', 'a', 'great', 'thing.']
['@ABCPolitics', 'piles', 'on', 'more', 'white', 'people', 'with', 'a', 'thuggish', 'past.']
['@ABCPolitics', '@realDonaldTrump', 'wait', 'till', 'November', 

['Are', 'You', 'Too', 'Busy?', 'Five', 'Signs', 'of', 'Chronic', 'Stress', '#health', '#wellness', '#business', '#culture', '#stress']
['are', 'you', 'trying', 'to', 'fool', 'me', 'with', 'those', 'bullshits', 'over', 'there']
['Arguing', 'with', 'an', 'idiot', 'is', 'one', 'of', 'the', 'most', 'frustrating', 'things', 'ever.']
['ariana', 'actually', 'looks', 'like', 'a', 'princess', 'in', 'this', 'elegant', 'dress', 'and', 'i', 'love', 'how', 'she', 'always', 'keeps', 'it', 'classy']
['Ariana', 'and', 'Justin', 'as', 'a', 'sims!', 'Ik', 'they', "don't", 'look', 'like', 'them,', 'but', 'I', 'tried', 'and', 'I', 'made', 'them', 'just', 'for', 'fun']
['@ArianaGrande', 'Bby', 'you', 'are', 'beautiful', 'in', 'every', 'way!', "I'll", 'always', 'support', 'you,', 'keep', 'singing', 'and', 'make', 'the', 'world', 'shines', '😘', 'i', 'love', 'u.']
['@ArianaGrande', 'Cause', 'all', 'of', 'me', 'loves', 'all', 'of', 'you,', 'love', 'your', 'curves', 'and', 'all', 'your', 'edges', 'All', 'your',

['@BrunoMars', 'your', 'mom', 'loved', 'you,', 'and', 'she', 'still', 'love', 'you.', 'And', 'we', 'will', 'love', 'you', 'forever.']
['bruuuuuuuuuh', 'the', 'epitome', 'of', 'black', 'mothers', 'right', 'here.', 'Lmfaoo', '"', 'And', 'Guess', 'what?', 'You', 'finna', 'get', 'a', 'Mf', 'ass', 'whoopin', '"']
['@bryan1996callum', 'good', 'stuff!', 'I', 'no', 'cant', 'wait', 'for', 'the', 'season', 'to', 'start!', 'Nice', 'one!', 'We', 'will', 'sort', 'some', 'dates', 'and', 'see', 'wots', 'best', 'for', 'u', 'guys!']
['@bryanglenn24', 'No', 'sir', 'I', 'have', 'not.', 'He', 'does', 'a', 'good', 'enough', 'job', 'scaring', 'himself', 'on', 'his', 'own.', '#GoGreen']
['@bryantluna_', 'LMAO', 'not', 'you', 'bestfriend', '😭']
['@brycepugh', '@mistergoats', 'which', 'means', 'I', 'will', 'totally', 'NOT', 'avoid', 'obvy.', '#Rebel', '#DontTellMeWhatToDo']
['Bryson', 'tiller-two', 'hearts', 'been', 'stuck', 'in', 'my', 'head', 'all', 'damn', 'day', 'well', 'the', 'ending', 'like', 'dammiiittt

['@DailyMailUK', 'Civil', 'Servants', 'are', 'not', 'employed', 'to', 'be', 'either', 'Europhile', 'or', 'Sceptic', 'but', 'only', 'to', 'do', 'the', 'will', 'of', 'the', 'PEOPLE', 'expressed', 'through', 'Govt']
['@DailyMailUK', 'just', 'read', 'about', 'ccjs.', 'Since', '2011', 'county', 'courts', 'have', 'NO', 'power', 'due', 'to', 'halsbury', 'law', '2011']
['@DailyMailUK', '@MailOnline', '@KTHopkins', 'how', 'do', 'you', 'think', 'these', 'people', 'are', 'getting', 'into', 'our', 'country', 'government', 'are', 'allowing', 'it']
['@DailyMail', '"', 'You', 'see', 'the', 'railing', 'here:', 'tells', 'you', "don't", 'go', 'over', '&', 'try', '2take', 'pictures;', 'people', 'take', 'chances;', 'ends', 'up', 'like', 'this.', '"', '#darwinaward']
['@DailyMirror', '@BryantDjbryant', 'If', 'he', 'gets', 'his', 'RMN-he', 'will', 'be', 'getting', 'help', 'with', 'that', 'too.', 'Probably', 'a', 'degree!']
['@DailyMirror', 'oh', 'the', 'outrage!', 'Just', 'ignore', 'it', 'if', 'you', "don't

...

['OMG', 'I', 'luv', 'friends', 'that', 'disappear', 'when', 'they', 'get', 'into', 'relationships', "it's", 'seriously', 'my', 'favorite', 'thing', 'ever.', '#not', '#sarcasm']
['Omg', 'I', 'only', 'shaved', 'one', 'leg', '#sarcasm']
['Omg', 'its', 'raining', 'what', 'a', 'surprise', '#sarcasm']
['omg', 'look', 'at', 'her', 'face...', '#not', '#sarcasm']
['OMG', '@NyleDiMarco', 'CRYING', 'ABOUT', 'HOW', 'GREAT', 'HIS', 'MOM', 'IS', 'MY', 'HEART', 'JUST', 'EXPLODED', '#sarcasm']
['Omg', '@Oliviaaaa_____', 'is', 'following', 'me', "I'm", 'dyyyyyiiiinnng...', '#not', '#sarcasm']
['OMGOMG', "can't", 'wait', 'for', 'school', 'tomorrow!', ':D', '#sarcasm']
['Omg', '@TheBoyFromEgypt', 'is', 'The', 'best,', 'he', 'lowkey', 'kept', 'on', 'giving', 'me', 'sour', 'patch', 'kids', 'during', 'algebra', '✊', '#sarcasm']
['OMG', 'this', 'is', 'Freaky!', 'Have', '8', 'beers', '&', '3', 'shots,', 'go', 'to', 'your', 'phone', 'the', 'next', 'day,', 'press', "'Recently", 'Dialed', "'", '&', 'the', 'name'

['RT', 'Me', '-', '143', 'She', '-?', 'Me', '-', 'I', 'Love', 'You', 'She', '-', '1419', 'Me', '-?', '😞', 'She', '-', 'I', 'have', 'a', 'boyfriend', '#sarcasm']
['RT', 'Me', ':', 'Aah!', 'I', 'look', 'beautiful', 'today...', 'no', 'comments!', 'Toe', 'nails', ':', 'bitch', 'please!', '#sarcasm']
['RT', '*Meanwhile*', 'Mother', ':', 'we', 'like', 'to', 'name', 'her', 'Sara.', 'Dr.', ':', 'that', 'name', 'is', 'already', 'taken!', 'Try', ':', 'sara123', 'or', 'sara_2016', '#sarcasm']
['RT', 'me', ':', 'better', 'check', 'my', 'phone', 'for', 'some', 'texts..', '*checks', 'phone*', 'me', ':', 'better', 'get', 'some', 'friends', '#sarcasm']
['RT', 'Me', '-', 'But', "it's", '2am!', 'Stomach', '-', "Don't", 'teach', 'me', 'when', 'to', 'eat', 'and', 'when', 'not', 'to!', '#sarcasm']
['RT', 'Me', '-Doc,', 'i', 'took', 'my', 'medicine', '6', "'o", 'clock', 'today', 'Doc', '-i', 'told', 'u', 'to', 'take', '9', 'Me', '-i', 'know,', 'but', 'i', 'wanted', 'to', 'surprise', 'the', 'bacterias', '#sa

['So', 'nice', 'to', 'come', 'home', 'to', 'my', 'parents', 'house', 'to', 'have', 'them', 'buy', 'no', 'food', 'just', 'because', 'they', 'know', 'how', 'fat', 'I', 'am', '#sarcasm']
['So', 'nice', 'waking', 'up', 'to', 'this..', '#NOT', 'more', 'like', 'my', 'dig', 'Gus', 'clawing', 'my', 'face', 'at', '6AM', 'Happy', '#Wednesday', '#sarcasm']
['@sONICmEW152', 'awww', 'cute', 'c', ':', 'I', 'love', 'your', 'sneeze.', 'But', 'not', 'as', 'much', 'as', 'your', 'pretty', 'singing', '#sarcasm']
['So', '#not', 'a', 'productive', 'member', 'of', 'society', 'today.', 'Ate', 'a', '#cannacookie', 'and', 'now', 'just', 'playing', 'Left', 'For', 'Dead', '2', '&', 'listening', 'to', 'Pandora.', '#sarcasm']
['So', 'now', 'guess', 'whos', 'covered', 'in', 'hives', 'and', 'rashes', 'and', 'welts', 'from', 'itching', '😰', '#sarcasm']
['So', 'now', 'I', "can't", 'sleep', 'apparently.', "It's", 'going', 'to', 'be', 'a', 'good', 'day', '😳😳', '#not', '😒', '#sarcasm']
['so', 'now', 'my', 'star', 'wars', 

['Today', 'I', 'devoted', 'myself', 'to', 'doing', 'nothing,', 'it', 'was', 'great', '#sarcasm']
['Today', "I'm", 'thankful', 'that', 'we', 'have', 'a', 'herd', 'of', 'elephants', 'living', 'upstairs', 'from', 'us', '🐘', '#blessed', '#sarcasm']
['Today', 'is', 'a', 'stay', 'in', 'bed,', 'pull', 'the', 'blankets', 'over', 'your', 'head,', 'and', 'pretend', 'ur', 'on', 'an', 'adventure', 'in', 'a', "kangaroo's", 'pouch', 'type', 'of', 'day', '#sarcasm']
['Today', 'I', 'saw', 'a', 'biker', 'ride', 'their', 'bike', 'on', 'the', 'side', 'of', 'the', 'road,', 'not', 'the', 'middle', 'of', 'the', 'lane', '#lol', '#jk', '#not', '#sarcasm']
['Today', 'I', 'saw', 'a', 'sign', 'for', 'a', 'suicide', 'helpline', 'on', 'the', 'back', 'of', 'a', 'bus.', 'I', "couldn't", 'help', 'but', 'think,', 'it', 'would', 'probably', 'work', 'much', 'better', 'on', 'front.', '#sarcasm']
['Today', 'I', 'saw', 'something', 'that', 'reminded', 'me', 'of', 'you.', 'But', "don't", 'worry,', 'I', 'flushed', 'and', 'ev

['Wipe', 'your', 'mouth.', "There's", 'still', 'a', 'tiny', 'bit', 'of', 'bullshit', 'around', 'your', 'lips.', '#sarcasm']
['wip', 'pls', 'dont', 'retweet', 'im', 'drawing', 'babies', 'i', 'love', 'these', 'babies', '#sarcasm']
['Wishing', 'you', 'could', 'punch', 'someone', 'in', 'the', 'face', 'with', 'no', 'consequences.', '#sarcasm']
['Wish', 'I', 'still', 'had', 'that', 'feeling.', 'Lol', 'it', 'burnt', 'out.', 'Not', 'even', 'fun', 'anymore.', '#sarcasm']
['Wish', 'I', 'took', 'a', 'before', 'and', 'after', 'photo', 'of', 'me', 'trying', 'out', 'this', 'hair', 'mask.', 'I', 'think', "I'm", 'going', 'to', 'order', 'more', 'because', 'this', 'shit', 'is', 'awesome', '#sarcasm']
['wish', 'I', "wasn't", 'such', 'a', 'piece', 'of', 'shit', 'lol', '#sarcasm']
['Wish', 'I', 'woulda', 'knew', 'this', 'shit', 'back', 'then!', '#sarcasm']
['Wish', 'I', 'would', 'be', 'paying', 'for', 'a', 'dance', 'and', "can't", 'run', 'that', 'pussy', 'you', "ain't", 'gettin', 'shit', '#sarcasm']
['wish

In [91]:
i = 0
xxx = []
stop_words = set(stopwords.words('english'))
for string in stmt:
    string = string.strip().lower()
    cvb = []
    i += 1
    xx = string.split()
    cc = xx.copy()
    for x in cc:
        # if x in stop_words:
        #     continue
        x = x.strip()
        if str(x).startswith("@") or str(x).startswith("$") or str(x).startswith("http") or str(x).startswith("#"):
            continue
        if (x in emoji_dict):
            x = emoji_dict.get(x).split('_')
            cvb.extend(x)
            continue
        if x in repl:
            print('inn', x)
            x = repl.get(x)
            x = x.strip().split()
            print(x)
            cvb.extend(x)
            continue
        cvb.append(x)
    # print(xx)
    sss = cvb[0]
    for c in cvb[1:]:
        sss = sss + " " + c
    # ss = [' '.join(c) for c in xx]
    # xxx.append(sss)
    # print(sss)
    xxx.append(sss)
    if i == 20:
        break
appendFile = open('norm_text_rm-stopdemo1.txt','a')
# print(xxx)
for vb in xxx:
    appendFile.write(str(vb) + '\n')
appendFile.close()

inn i'm
['i', 'am']
inn yay!
['good']
inn can't
['can', 'not']
inn don't
['do', 'not']
inn i'm
['i', 'am']
inn :)
['smile']
inn didn't
['did', 'not']
inn can't
['can', 'not']


In [123]:
pos = []
neg = []
for i in range(len(stmt)):
    if label[i] == 0:
        neg.append(stmt[i])
    else:
        pos.append(stmt[i])

In [124]:
len(pos), len(neg)

(18488, 21292)

In [126]:
xxx = []
# stop_words = set(stopwords.words('english'))
for string in neg:
    string = string.strip().lower()
    cvb = []
    xx = string.split()
    cc = xx.copy()
    for x in cc:
        # if x in stop_words:
        #    continue
        x = x.strip()
        if str(x).startswith("@") or str(x).startswith("$") or str(x).startswith("http") or str(x).startswith("#"):
            continue
        if (x in emoji_dict):
            x = emoji_dict.get(x).split('_')
            cvb.extend(x)
            continue
        if x in repl:
            # print('inn', x)
            x = repl.get(x)
            x = x.strip().split()
            # print(x)
            cvb.extend(x)
            continue
        cvb.append(x)
    # print(xx)
    if len(cvb) != 0:
        sss = cvb[0]
        for c in cvb[1:]:
            sss = sss + " " + c
        xxx.append(sss)
appendFile = open('neg.txt','a')
# print(xxx)
for vb in xxx:
    appendFile.write(str(str(vb).encode("utf-8")))
    appendFile.write("\n")
appendFile.close()
'''
    string = sss
    string = re.sub(r"[^A-Za-z0-9(),!?\'\`]", " ", string)
    string = re.sub(r"\'s", " \'s", string)
    string = re.sub(r"\'ve", " \'ve", string)
    string = re.sub(r"n\'t", " n\'t", string)
    string = re.sub(r"\'re", " \'re", string)
    string = re.sub(r"\'d", " \'d", string)
    string = re.sub(r"\'ll", " \'ll", string)
    string = re.sub(r",", " , ", string)
    string = re.sub(r"!", " ! ", string)
    string = re.sub(r"\(", " \( ", string)
    string = re.sub(r"\)", " \) ", string)
    string = re.sub(r"\?", " \? ", string)
    string = re.sub(r"\s{2,}", " ", string)
'''

'\n    string = sss\n    string = re.sub(r"[^A-Za-z0-9(),!?\'\\`]", " ", string)\n    string = re.sub(r"\'s", " \'s", string)\n    string = re.sub(r"\'ve", " \'ve", string)\n    string = re.sub(r"n\'t", " n\'t", string)\n    string = re.sub(r"\'re", " \'re", string)\n    string = re.sub(r"\'d", " \'d", string)\n    string = re.sub(r"\'ll", " \'ll", string)\n    string = re.sub(r",", " , ", string)\n    string = re.sub(r"!", " ! ", string)\n    string = re.sub(r"\\(", " \\( ", string)\n    string = re.sub(r"\\)", " \\) ", string)\n    string = re.sub(r"\\?", " \\? ", string)\n    string = re.sub(r"\\s{2,}", " ", string)\n'

In [132]:
fp = open('pos.txt', 'r')
fp1 = open('pos1.txt', 'a')
ll = fp.readlines()
for c in ll:
    if c[:2] == "b'" or c[:2] == "b\"":
        c = c[2:-2]
    fp1.write(c + '\n')
fp1.close()
fp.close()

In [133]:
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences

In [134]:
fp1 = open('pos1.txt', 'r')
posli = fp1.readlines()
fp2 = open('neg1.txt', 'r')
negli = fp2.readlines()

In [141]:
np.max([len(x.split()) for x in posli1])

126

In [139]:
posli1 = []
c = '\\'
for b in posli:
    nnn = []
    x = b.split()
    for mm in x:
        if c in mm:
            continue
        nnn.append(mm)
    sa = nnn[0]
    for vv in nnn:
        sa += vv + " "
    posli1.append(sa)
posli1

['beingbeing sore is the best and the worst feeling in the world ',
 'expectingexpecting is my favorite crime and disappointment is always my punishment.. disappointed but relieved face smiling face with smiling eyes ',
 'happyhappy birthday to me. yay. ',
 'latelate nights early mornings hmmm & i say thank yooooooo kissing face with closed eyes smiling face with heart shaped eyes ',
 'latelate nights, early mornings is how i live my life. ',
 'latelate nights early mornings smiling face with heart shaped eyes face throwing a kiss ',
 'latelate nights early mornings, thank god for another day ',
 "latelate nights early mornings that's how much i want it. ",
 'latelate nights, early mornings weary face weary face weary face ',
 "05:35am05:35am & i've better gonna back 2 sleep now. last half hour ago i had annoying dream about my ex. why the hell i dream about guy i ",
 '100%100% failed both physics exams great ',
 "100%100% gonna have to go out for tea tonight because i'll either burn t

In [140]:
negli1 = []
c = '\\'
for b in negli:
    nnn = []
    x = b.split()
    for mm in x:
        if c in mm:
            continue
        nnn.append(mm)
    sa = nnn[0]
    for vv in nnn:
        sa += vv + " "
    negli1.append(sa)
negli1

['ii hope youre lurking rn. i want to listen to hallucination & wanna love you again live someday, pretty please?! loudly crying face loudly crying face loudly crying face ',
 '0505 really taught me a valuable lesson i am never gonna be late again! ',
 'nevernever had a voice to protest, so you fed me shit to digest. i wish i had a reason, my flaws are open season. ',
 'restrest in peace & love to you and your family ',
 '100100 days until christmas! evergreen tree soon ready yet ',
 'goodgood can not wait to be reunited with you huni! xx ',
 '100100 words short of the word requirement but i do not care, i am going to bed. ',
 'itit was nice hanging out this afternoon. i had a great time! ',
 '10k10k walk this morning. we did an awesome job. ',
 '1010 minutes to eat ',
 '1010 times one direction had the perfect love song for every relationship : ',
 "yetyet again if you list them on twitter you're garbage. ",
 'wow!wow! sweet butt for all of them i love smile ',
 "1111 o'clock cant com

In [172]:
dataa = []
m = 0
for i in posli1:
    dataa.append(posli1[m])
    m += 1
m = 0
for i in negli1:
    dataa.append(negli1[m])
    m += 1

In [175]:
# MAIN USED
tokenizer = Tokenizer(nb_words=125)
tokenizer.fit_on_texts(dataa)
seq = tokenizer.texts_to_sequences(dataa)
wi = tokenizer.word_index
print('Found %s unique tokens.' % len(wi))
dataa1 = pad_sequences(seq, maxlen=125)

c:\users\aa\appdata\local\programs\python\python35\lib\site-packages\keras\preprocessing\text.py:145: UserWarning: The `nb_words` argument in `Tokenizer` has been renamed `num_words`.
  warnings.warn('The `nb_words` argument in `Tokenizer` '


Found 27547 unique tokens.


In [149]:
tokenizer = Tokenizer(nb_words=125)
tokenizer.fit_on_texts(negli1)
negseq = tokenizer.texts_to_sequences(negli1)
negwi = tokenizer.word_index
print('Found %s unique tokens.' % len(negwi))
negdata = pad_sequences(negseq, maxlen=125)

c:\users\aa\appdata\local\programs\python\python35\lib\site-packages\keras\preprocessing\text.py:145: UserWarning: The `nb_words` argument in `Tokenizer` has been renamed `num_words`.
  warnings.warn('The `nb_words` argument in `Tokenizer` '


Found 21004 unique tokens.


In [150]:
len(posdata), len(negdata)

(18487, 21291)

In [160]:
labell = []
m, k = 0, 0
dataa = []
for c in range(39778):
    if c > 18487:
        labell.append([0, 1])     # NOT SARCASM
    else:
        labell.append([1, 0])     # SARCASM

In [163]:
len(labell), len(dataa)

(39778, 39778)

In [176]:
embeddings_index = {}
f = open('glove.twitter.27B.25d.txt', 'r', encoding="utf8")
for line in f.readlines():
    values = line.split()
    word = values[0]
    coefs = np.asarray(values[1:], dtype='float32')
    embeddings_index[word] = coefs
f.close()
print('Found %s word vectors.' % len(embeddings_index))

Found 1193515 word vectors.


In [177]:
dataaemat = np.zeros((len(dataa) + 1, 25))
for word, i in wi.items():
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None:
        # words not found in embedding index will be all-zeros.
        dataaemat[i] = embedding_vector

In [178]:
embedding_layer = Embedding(len(wi) + 1,
                            25,
                            weights=[dataaemat],
                            input_length=125,
                            trainable=False)

In [204]:
from keras.layers import Input, Dense, Dropout, Embedding, Flatten, LSTM, Conv1D, MaxPooling1D, GlobalMaxPool1D
from keras.models import Sequential, load_model, Model

In [185]:
from keras import backend as K
K.set_image_dim_ordering('tf')

In [188]:
sequence_input = Input(shape=(125,), dtype='int32')
embedded_sequences = embedding_layer(sequence_input)
x = Conv1D(128, 5, activation='relu')(embedded_sequences)
x = MaxPooling1D(5)(x)
x = Conv1D(128, 5, activation='relu')(x)
x = MaxPooling1D(5)(x)
#x = Conv1D(128, 5, activation='relu')(x)
#x = MaxPooling1D(35)(x)  # global max pooling
x = Flatten()(x)
x = Dense(128, activation='relu')(x)
preds = Dense(2, activation='softmax')(x)
model = Model(sequence_input, preds)
adam = Adam(lr=0.0001)
model.compile(loss='categorical_crossentropy',
              optimizer=adam,
              metrics=['acc'])
print(model.summary())

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_6 (InputLayer)         (None, 125)               0         
_________________________________________________________________
embedding_1 (Embedding)      (None, 125, 25)           688700    
_________________________________________________________________
conv1d_16 (Conv1D)           (None, 121, 128)          16128     
_________________________________________________________________
max_pooling1d_11 (MaxPooling (None, 24, 128)           0         
_________________________________________________________________
conv1d_17 (Conv1D)           (None, 20, 128)           82048     
_________________________________________________________________
max_pooling1d_12 (MaxPooling (None, 4, 128)            0         
_________________________________________________________________
flatten_1 (Flatten)          (None, 512)               0         
__________

In [195]:
len(dataa1), len(labell)

(39778, 39778)

In [196]:
from sklearn.model_selection import train_test_split
train_X, valid_X, train_y, valid_y = train_test_split(dataa1, labell, test_size = 0.15, random_state = 144) 

In [198]:
model.fit(train_X, train_y, validation_data=(valid_X, valid_y),
          epochs=50, batch_size=128, verbose = 1)

Train on 33811 samples, validate on 5967 samples
Epoch 1/50
33811/33811 [==============================] - 16s - loss: 0.6604 - acc: 0.5998 - val_loss: 0.6629 - val_acc: 0.5931
Epoch 2/50
33811/33811 [==============================] - 16s - loss: 0.6529 - acc: 0.6105 - val_loss: 0.6607 - val_acc: 0.5943
Epoch 3/50
33811/33811 [==============================] - 16s - loss: 0.6463 - acc: 0.6184 - val_loss: 0.6584 - val_acc: 0.5985
Epoch 4/50
33811/33811 [==============================] - 17s - loss: 0.6397 - acc: 0.6291 - val_loss: 0.6571 - val_acc: 0.6003
Epoch 5/50
33811/33811 [==============================] - 17s - loss: 0.6339 - acc: 0.6333 - val_loss: 0.6548 - val_acc: 0.6045
Epoch 6/50
33811/33811 [==============================] - 17s - loss: 0.6278 - acc: 0.6401 - val_loss: 0.6546 - val_acc: 0.6072
Epoch 7/50
33811/33811 [==============================] - 17s - loss: 0.6214 - acc: 0.6504 - val_loss: 0.6542 - val_acc: 0.6072
Epoch 8/50
33811/33811 [==============================]

KeyboardInterrupt: 

In [199]:
model.save('simple_acc62.h5')

In [223]:
sequence_input = Input(shape=(125,), dtype='int32')
embedded_sequences = embedding_layer(sequence_input)
x = Conv1D(128, 5, activation='relu')(embedded_sequences)
x = MaxPooling1D(5)(x)
x = Dropout(0.25)(x)
x = Conv1D(128, 5, activation='relu')(x)
x = MaxPooling1D(5)(x)
x = Dropout(0.25)(x)
x = Flatten()(x)
x = Dense(128, activation='relu')(x)
preds = Dense(2, activation='softmax')(x)
model1 = Model(sequence_input, preds)
adam = Adam(lr=0.0001)
model1.compile(loss='categorical_crossentropy',
              optimizer=adam,
              metrics=['acc'])
print(model1.summary())

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_22 (InputLayer)        (None, 125)               0         
_________________________________________________________________
embedding_1 (Embedding)      (None, 125, 25)           688700    
_________________________________________________________________
conv1d_49 (Conv1D)           (None, 121, 128)          16128     
_________________________________________________________________
max_pooling1d_31 (MaxPooling (None, 24, 128)           0         
_________________________________________________________________
dropout_31 (Dropout)         (None, 24, 128)           0         
_________________________________________________________________
conv1d_50 (Conv1D)           (None, 20, 128)           82048     
_________________________________________________________________
max_pooling1d_32 (MaxPooling (None, 4, 128)            0         
__________

In [201]:
train_X, valid_X, train_y, valid_y = train_test_split(dataa1, labell, test_size = 0.15, random_state = 42)

In [202]:
model1.fit(train_X, train_y, validation_data=(valid_X, valid_y),
          epochs=25, batch_size=128, verbose = 1)

Train on 33811 samples, validate on 5967 samples
Epoch 1/25
33811/33811 [==============================] - 23s - loss: 0.6897 - acc: 0.5362 - val_loss: 0.6874 - val_acc: 0.5483
Epoch 2/25
33811/33811 [==============================] - 19s - loss: 0.6854 - acc: 0.5487 - val_loss: 0.6856 - val_acc: 0.5492
Epoch 3/25
33811/33811 [==============================] - 18s - loss: 0.6825 - acc: 0.5578 - val_loss: 0.6827 - val_acc: 0.5534
Epoch 4/25
33811/33811 [==============================] - 18s - loss: 0.6801 - acc: 0.5669 - val_loss: 0.6819 - val_acc: 0.5534
Epoch 5/25
33811/33811 [==============================] - 19s - loss: 0.6768 - acc: 0.5762 - val_loss: 0.6753 - val_acc: 0.5745
Epoch 6/25
33811/33811 [==============================] - 18s - loss: 0.6715 - acc: 0.5857 - val_loss: 0.6770 - val_acc: 0.5648
Epoch 7/25
33811/33811 [==============================] - 18s - loss: 0.6664 - acc: 0.5911 - val_loss: 0.6673 - val_acc: 0.5844- ETA: 1s - lo
Epoch 8/25
33811/33811 [=================

In [203]:
model1.save('simple_withdropout_acc64.h5')

In [230]:
sequence_input = Input(shape=(125,), dtype='int32')
embedded_sequences = embedding_layer(sequence_input)
x = Conv1D(128, 5, activation='relu')(embedded_sequences)
x = MaxPooling1D(5)(x)
x = Dropout(0.25)(x)
x = Conv1D(128, 5, activation='relu')(x)
x = MaxPooling1D(5)(x)
# x = GlobalMaxPool1D()(x)
x = Dropout(0.25)(x)
x = Flatten()(x)
x = Dense(254, activation='relu')(x)
x = Dense(128, activation='relu')(x)
preds = Dense(2, activation='softmax')(x)
model3 = Model(sequence_input, preds)
adam = Adam(lr=0.0001)
model3.compile(loss='categorical_crossentropy',
              optimizer=adam,
              metrics=['acc'])
print(model3.summary())

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_26 (InputLayer)        (None, 125)               0         
_________________________________________________________________
embedding_1 (Embedding)      (None, 125, 25)           688700    
_________________________________________________________________
conv1d_57 (Conv1D)           (None, 121, 128)          16128     
_________________________________________________________________
max_pooling1d_38 (MaxPooling (None, 24, 128)           0         
_________________________________________________________________
dropout_39 (Dropout)         (None, 24, 128)           0         
_________________________________________________________________
conv1d_58 (Conv1D)           (None, 20, 128)           82048     
_________________________________________________________________
max_pooling1d_39 (MaxPooling (None, 4, 128)            0         
__________

In [226]:
train_X, valid_X, train_y, valid_y = train_test_split(dataa1, labell, test_size = 0.15, random_state = 7)

In [227]:
model3.fit(train_X, train_y, validation_data=(valid_X, valid_y),
          epochs=25, batch_size=128, verbose = 1)

Train on 33811 samples, validate on 5967 samples
Epoch 1/25
33811/33811 [==============================] - 21s - loss: 0.6894 - acc: 0.5357 - val_loss: 0.6858 - val_acc: 0.5557
Epoch 2/25
33811/33811 [==============================] - 20s - loss: 0.6846 - acc: 0.5504 - val_loss: 0.6840 - val_acc: 0.5520
Epoch 3/25
33811/33811 [==============================] - 20s - loss: 0.6811 - acc: 0.5601 - val_loss: 0.6800 - val_acc: 0.5634
Epoch 4/25
33811/33811 [==============================] - 21s - loss: 0.6758 - acc: 0.5773 - val_loss: 0.6785 - val_acc: 0.5604
Epoch 5/25
33811/33811 [==============================] - 17s - loss: 0.6700 - acc: 0.5863 - val_loss: 0.6686 - val_acc: 0.5944
Epoch 6/25
33811/33811 [==============================] - 18s - loss: 0.6633 - acc: 0.5953 - val_loss: 0.6629 - val_acc: 0.5968
Epoch 7/25
33811/33811 [==============================] - 21s - loss: 0.6570 - acc: 0.6026 - val_loss: 0.6582 - val_acc: 0.6008
Epoch 8/25
33811/33811 [==============================]

In [228]:
model3.save('simple_2xdense_acc64.h5')

In [233]:
tokenizer

In [ ]:
# MAIN USED
tokenizer = Tokenizer(nb_words=125)
tokenizer.fit_on_texts(dataa)
seq = tokenizer.texts_to_sequences(dataa)
wi = tokenizer.word_index
print('Found %s unique tokens.' % len(wi))
dataa1 = pad_sequences(seq, maxlen=125)

In [256]:
s = "I hate me" # SARCASM
testseq = tokenizer.texts_to_sequences([s])
testdata = pad_sequences(testseq, maxlen=125)
print(testseq, testdata)

[[2, 94, 16]] [[ 0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
   0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
   0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
   0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
   0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0  0
   0  0  2 94 16]]


In [257]:
ans = model3.predict(testdata)
ans

array([[ 0.50031716,  0.49968284]], dtype=float32)

In [217]:
sequence_input = Input(shape=(125,), dtype='int32')
embedded_sequences = embedding_layer(sequence_input)
x = Conv1D(128, 5, activation='relu')(embedded_sequences)
# x = MaxPooling1D(5)(x)
x = Dropout(0.15)(x)
x = Conv1D(128, 5, activation='relu')(x)
# x = GlobalMaxPool1D()(x)
x = Dropout(0.15)(x)
x = LSTM(32, kernel_initializer='he_normal', activation='sigmoid', dropout=0.25, return_sequences=True)(x)
x = LSTM(32, kernel_initializer='he_normal', activation='sigmoid', dropout=0.25, return_sequences=True)(x)
x = Flatten()(x)
x = Dense(128, activation='relu')(x)
preds = Dense(2, activation='softmax')(x)
model2 = Model(sequence_input, preds)
adam = Adam(lr=0.0001)
model2.compile(loss='categorical_crossentropy',
              optimizer=adam,
              metrics=['acc'])
print(model2.summary())

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_18 (InputLayer)        (None, 125)               0         
_________________________________________________________________
embedding_1 (Embedding)      (None, 125, 25)           688700    
_________________________________________________________________
conv1d_40 (Conv1D)           (None, 121, 128)          16128     
_________________________________________________________________
dropout_23 (Dropout)         (None, 121, 128)          0         
_________________________________________________________________
conv1d_41 (Conv1D)           (None, 117, 128)          82048     
_________________________________________________________________
dropout_24 (Dropout)         (None, 117, 128)          0         
_________________________________________________________________
lstm_9 (LSTM)                (None, 117, 32)           20608     
__________

In [215]:
train_X, valid_X, train_y, valid_y = train_test_split(dataa1, labell, test_size = 0.15, random_state = 7)

In [219]:
model2.fit(train_X, train_y, validation_data=(valid_X, valid_y),
          epochs=5, batch_size=512, verbose = 1)

Train on 33811 samples, validate on 5967 samples
Epoch 1/5
33811/33811 [==============================] - 135s - loss: 0.6937 - acc: 0.5230 - val_loss: 0.6920 - val_acc: 0.5359
Epoch 2/5
33811/33811 [==============================] - 129s - loss: 0.6930 - acc: 0.5226 - val_loss: 0.6919 - val_acc: 0.5359
Epoch 3/5
33811/33811 [==============================] - 133s - loss: 0.6933 - acc: 0.5245 - val_loss: 0.6923 - val_acc: 0.5359
Epoch 4/5
 1536/33811 [>.............................] - ETA: 119s - loss: 0.7056 - acc: 0.4844

KeyboardInterrupt: 

In [179]:
'''
model = Sequential()
model.add(embedding_layer)
model.add(Convolution1D(hidden_units, 3, kernel_initializer='he_normal', padding='valid', activation='sigmoid', input_shape=(1, maxlen)))
# model.add(MaxPooling1D(pool_size=3))
model.add(Convolution1D(hidden_units, 3, kernel_initializer='he_normal', padding='valid', activation='sigmoid', input_shape=(1, maxlen - 2)))
# model.add(MaxPooling1D(pool_size=3))
# model.add(Dropout(0.25))
model.add(LSTM(hidden_units, kernel_initializer='he_normal', activation='sigmoid', dropout=0.5, return_sequences=True))
model.add(LSTM(hidden_units, kernel_initializer='he_normal', activation='sigmoid', dropout=0.5))
model.add(Dense(hidden_units, kernel_initializer='he_normal', activation='sigmoid'))
model.add(Dense(2))
model.add(Activation('softmax'))
adam = Adam(lr=0.0001)
model.compile(loss='categorical_crossentropy', optimizer=adam, metrics=['accuracy'])
print('No of parameter:', model.count_params())
print(model.summary())
'''

ValueError: Layer weight shape (27548, 25) not compatible with provided weight shape (39779, 25)